In [ ]:
import gradio as gr
from langchain.callbacks.streaming_stdout import StreamingStdOutCallbackHandler
from langchain.chains import LLMChain
from langchain_community.llms import GPT4All
from langchain_core.prompts import PromptTemplate
from langchain.memory import ConversationBufferMemory
from langchain_core.prompts import (
    ChatPromptTemplate,
    MessagesPlaceholder,
    SystemMessagePromptTemplate,
    HumanMessagePromptTemplate,
)

def response(input, history):
    # Path to your local GPT4All model
    local_path = "C:/Users/chris/AppData/Local/nomic.ai/GPT4All/Meta-Llama-3-8B-Instruct.Q4_0.gguf"

    # Callbacks support token-wise streaming
    callbacks = [StreamingStdOutCallbackHandler()]

    # Initialize GPT4All model
    llm = GPT4All(streaming= True, model=local_path, backend="gptj", callbacks=callbacks, verbose=False)

    prompt = ChatPromptTemplate(
        messages=[
            SystemMessagePromptTemplate.from_template(
                "You are a cute anime chatbot having a conversation with a human."
            ),
            # The `variable_name` here is what must align with memory
            MessagesPlaceholder(variable_name="{history}"),
            HumanMessagePromptTemplate.from_template("{question}")
        ]
    )

    # Initialize conversation memory
    memory = ConversationBufferMemory(memory_key="{history}", return_messages=True)
    #memory = history

    # Create an LLMChain instance for the conversation
    conversation = LLMChain(
        llm=llm,
        prompt=prompt,
        verbose=False,
        memory=memory
    )

    # Generate a response using the input and the LLMChain
    response = conversation.invoke(input={"question": input})["text"]

    return response

gr.ChatInterface(response).launch()


In [ ]:
# Local Llama 3 Chatbot

In [109]:
import ollama
import gradio as gr
def chat(question, history):
  history_format = []
  for human, assistant in history:
      history_format.append({"role": "user", "content": human})
      history_format.append({"role": "assistant", "content":assistant})
  history_format.append({'role': 'user', 'content': question})

  messages=history_format
  stream = ollama.chat(model='llama3', messages=messages)
  #print(history_format)
  return stream['message']['content']

# Gradio interface
assistant_icon = gr.Image(value="C:/Users/chris/Downloads/japanese-lama-ghibli-artstyle.jpeg", width=32, height=32)  # adjust the size as needed
assistant_img = gr.Image(value="C:/Users/chris/Downloads/japanese-lama-ghibli-artstyle.jpeg", elem_id="assistant_img")
gr.ChatInterface(fn=chat, title="Chat Bot",chatbot=gr.Chatbot(height=300)).launch()

Running on local URL:  http://127.0.0.1:7919

To create a public link, set `share=True` in `launch()`.
